In [1]:
import platform

import numpy as np

import plotly.graph_objects as go
import os
import plotly.io as pio
from plotly.subplots import make_subplots

import scipy
from scipy import optimize, special
from scipy.stats import chi2, nct, norm, t

pio.templates.default = "plotly_white"
pio.renderers.default = os.environ.get("PLOTLY_RENDERER", "notebook")

np.set_printoptions(precision=4, suppress=True)
rng = np.random.default_rng(7)

print("Python", platform.python_version())
print("NumPy", np.__version__)
print("SciPy", scipy.__version__)


Python 3.12.9
NumPy 1.26.2
SciPy 1.15.0


In [2]:
def nct_pdf(x: np.ndarray, df: float, nc: float) -> np.ndarray:
    x = np.asarray(x, dtype=float)
    return nct.pdf(x, df, nc)


def nct_logpdf(x: np.ndarray, df: float, nc: float) -> np.ndarray:
    x = np.asarray(x, dtype=float)
    return nct.logpdf(x, df, nc)


def nct_cdf(x: np.ndarray, df: float, nc: float) -> np.ndarray:
    x = np.asarray(x, dtype=float)
    # Same as nct.cdf, but explicitly shows the specialized implementation SciPy uses.
    return special.nctdtr(df, nc, x)


In [3]:
def _e_scaled_inv_chi_power(df: float, k: int) -> float:
    """E[(df/V)^(k/2)] for V ~ chi2(df). Exists iff df > k."""
    if df <= k:
        return np.nan
    return (df / 2) ** (k / 2) * special.gamma((df - k) / 2) / special.gamma(df / 2)


def nct_moments_closed_form(df: float, nc: float):
    """Mean/variance/skewness/excess kurtosis from the stochastic representation.

    Returns (mean, var, skew, exkurt). Values are NaN when the moment does not exist.
    """
    # Moments of Y ~ Normal(nc, 1)
    y1 = nc
    y2 = nc**2 + 1.0
    y3 = nc**3 + 3.0 * nc
    y4 = nc**4 + 6.0 * nc**2 + 3.0

    s1 = _e_scaled_inv_chi_power(df, 1)
    s2 = _e_scaled_inv_chi_power(df, 2)
    s3 = _e_scaled_inv_chi_power(df, 3)
    s4 = _e_scaled_inv_chi_power(df, 4)

    m1 = y1 * s1 if df > 1 else np.nan
    m2 = y2 * s2 if df > 2 else np.nan
    m3 = y3 * s3 if df > 3 else np.nan
    m4 = y4 * s4 if df > 4 else np.nan

    if not np.isfinite(m1) or not np.isfinite(m2):
        return m1, np.nan, np.nan, np.nan

    var = m2 - m1**2
    if not np.isfinite(var) or var <= 0:
        return m1, var, np.nan, np.nan

    if not np.isfinite(m3):
        return m1, var, np.nan, np.nan

    mu3 = m3 - 3 * m1 * m2 + 2 * m1**3
    skew = mu3 / (var ** 1.5)

    if not np.isfinite(m4):
        return m1, var, skew, np.nan

    mu4 = m4 - 4 * m1 * m3 + 6 * (m1**2) * m2 - 3 * m1**4
    exkurt = mu4 / (var**2) - 3

    return m1, var, skew, exkurt


# Quick numeric cross-check vs SciPy (avoid nc==0 exactly due to a corner-case in some SciPy versions)
for df, nc in [(10.0, 1.2), (6.0, 0.1), (3.5, -1.0)]:
    m, v, s, k = nct_moments_closed_form(df, nc)
    m_s, v_s, s_s, k_s = nct.stats(df, nc, moments="mvsk")
    print(f"df={df:>4}, nc={nc:>5} | closed-form mvsk = {m: .6f}, {v: .6f}, {s: .6f}, {k: .6f}")
    print(f"                scipy     mvsk = {m_s: .6f}, {v_s: .6f}, {s_s: .6f}, {k_s: .6f}")


df=10.0, nc=  1.2 | closed-form mvsk =  1.300467,  1.358786,  0.472341,  1.349288
                scipy     mvsk =  1.300467,  1.358786,  0.472341,  1.349288
df= 6.0, nc=  0.1 | closed-form mvsk =  0.115124,  1.501746,  0.093929,  3.017647
                scipy     mvsk =  0.115124,  1.501746,  0.093929,  3.017647
df= 3.5, nc= -1.0 | closed-form mvsk = -1.304653,  2.964547, -4.448490,  nan
                scipy     mvsk = -1.304653,  2.964547, -4.448490,  nan


In [4]:
x = np.linspace(-8, 8, 1200)

fig = make_subplots(
    rows=1,
    cols=2,
    subplot_titles=("Vary df (nc fixed)", "Vary nc (df fixed)"),
)

# Left: varying df
nc_fixed = 1.5
for df in [2.5, 5, 15, 80]:
    fig.add_trace(
        go.Scatter(x=x, y=nct_pdf(x, df, nc_fixed), name=f"df={df}, nc={nc_fixed}", mode="lines"),
        row=1,
        col=1,
    )

# Right: varying nc
df_fixed = 10
for nc in [-3, -1.5, 0.0, 1.5, 3.0]:
    fig.add_trace(
        go.Scatter(x=x, y=nct_pdf(x, df_fixed, nc), name=f"df={df_fixed}, nc={nc}", mode="lines"),
        row=1,
        col=2,
    )

fig.update_layout(height=420, width=980, title_text="Noncentral t: PDF shape changes")
fig.update_xaxes(title_text="x")
fig.update_yaxes(title_text="density")
fig.show()


In [5]:
def nct_neg_loglik(params: np.ndarray, data: np.ndarray) -> float:
    df, nc = float(params[0]), float(params[1])
    if not np.isfinite(df) or df <= 0 or not np.isfinite(nc):
        return np.inf
    return -float(np.sum(nct_logpdf(data, df, nc)))


# Synthetic example: recover parameters via numerical MLE
true_df, true_nc = 8.0, 1.25
sample = nct.rvs(true_df, true_nc, size=1500, random_state=rng)

res = optimize.minimize(
    nct_neg_loglik,
    x0=np.array([10.0, 0.5]),
    args=(sample,),
    bounds=[(1e-6, None), (None, None)],
)

print("True   (df, nc):", (true_df, true_nc))
print("MLE    (df, nc):", tuple(res.x))
print("Success:", res.success)


True   (df, nc): (8.0, 1.25)
MLE    (df, nc): (8.194098582508634, 1.2025931855233258)
Success: True


In [6]:
def nct_rvs_numpy(df: float, nc: float, size: int, rng: np.random.Generator) -> np.ndarray:
    if df <= 0:
        raise ValueError("df must be > 0")
    z = rng.standard_normal(size) + nc
    v = rng.chisquare(df, size=size)
    return z / np.sqrt(v / df)


# Sanity-check: Monte Carlo mean/variance vs theory
df, nc = 10.0, 1.2
x_mc = nct_rvs_numpy(df, nc, size=300_000, rng=rng)

m_theory, v_theory, *_ = nct_moments_closed_form(df, nc)

print("MC mean/var:", float(x_mc.mean()), float(x_mc.var()))
print("Theory mean/var:", float(m_theory), float(v_theory))


MC mean/var: 1.302083304452847 1.356864236401281
Theory mean/var: 1.3004667695269725 1.35878618135608


In [7]:
def ecdf(x: np.ndarray):
    xs = np.sort(np.asarray(x, dtype=float))
    ps = (np.arange(1, xs.size + 1) / xs.size)
    return xs, ps


df, nc = 8.0, 1.5
x_grid = np.linspace(-8, 8, 1500)

samples = nct_rvs_numpy(df, nc, size=80_000, rng=rng)

fig = make_subplots(
    rows=1,
    cols=2,
    subplot_titles=("PDF + Monte Carlo histogram", "CDF + empirical CDF"),
)

# PDF + histogram
fig.add_trace(
    go.Histogram(
        x=samples,
        nbinsx=120,
        histnorm="probability density",
        name="samples",
        opacity=0.55,
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Scatter(x=x_grid, y=nct_pdf(x_grid, df, nc), name="theoretical PDF", mode="lines"),
    row=1,
    col=1,
)

# CDF + ECDF
xs, ps = ecdf(samples)
fig.add_trace(
    go.Scatter(x=x_grid, y=nct_cdf(x_grid, df, nc), name="theoretical CDF", mode="lines"),
    row=1,
    col=2,
)
fig.add_trace(
    go.Scatter(x=xs[::50], y=ps[::50], name="empirical CDF", mode="markers", marker=dict(size=4)),
    row=1,
    col=2,
)

fig.update_layout(height=430, width=980, title_text=f"Noncentral t (df={df}, nc={nc})")
fig.update_xaxes(title_text="x")
fig.update_yaxes(title_text="density", row=1, col=1)
fig.update_yaxes(title_text="F(x)", row=1, col=2)
fig.show()


In [8]:
df, nc = 12.0, -0.75
x = np.array([-2.0, 0.0, 2.0])

print("pdf:", nct.pdf(x, df, nc))
print("cdf:", nct.cdf(x, df, nc))
print("rvs:", nct.rvs(df, nc, size=5, random_state=rng))
print("entropy:", nct.entropy(df, nc))

# Fit example (standardized loc=0, scale=1)
data = nct.rvs(9.0, 1.1, size=4000, random_state=rng)
df_hat, nc_hat, loc_hat, scale_hat = nct.fit(data, floc=0.0, fscale=1.0)

print("fit df, nc:", df_hat, nc_hat)


pdf: [0.1774 0.2949 0.0125]
cdf: [0.1311 0.7734 0.9942]
rvs: [-2.426  -0.1903 -0.34   -0.0526 -1.8375]
entropy: 1.5144120934998153


fit df, nc: 9.19392060339923 1.1072185503404517


In [9]:
def power_two_sided_t(n: int, alpha: float, mu_minus_mu0: float, sigma: float = 1.0) -> float:
    df = n - 1
    delta = np.sqrt(n) * (mu_minus_mu0 / sigma)
    crit = t.isf(alpha / 2, df)
    return float(nct.sf(crit, df, delta) + nct.cdf(-crit, df, delta))


alpha = 0.05
n = 20
sig = 1.0

effects = np.linspace(0.0, 1.2, 61)
powers = np.array([power_two_sided_t(n, alpha, eff, sigma=sig) for eff in effects])

fig = go.Figure(
    data=[go.Scatter(x=effects, y=powers, mode="lines", name="power")],
    layout=go.Layout(
        title=f"Two-sided one-sample t-test power (n={n}, alpha={alpha})",
        xaxis_title="effect (mu - mu0) in units of sigma",
        yaxis_title="power",
        yaxis=dict(range=[0, 1]),
    ),
)
fig.show()


In [10]:
# Bayesian-flavored example: predictive distribution of T under a prior on the standardized effect d
# d = (mu - mu0)/sigma, delta = sqrt(n)*d

n = 20
nu = n - 1

tau = 0.4  # prior std on standardized effect size d
m = 120_000

# Prior on effect size -> prior on delta
prior_d = rng.normal(0.0, tau, size=m)
prior_delta = np.sqrt(n) * prior_d

# Predictive sampling: sample delta, then sample T | delta ~ nct(nu, delta)
# (NumPy-only sampler using the nct construction)
z = rng.standard_normal(m) + prior_delta
v = rng.chisquare(nu, size=m)
t_pred = z / np.sqrt(v / nu)

a = 0.05
crit = t.isf(a / 2, nu)
print("Prior predictive P(reject H0):", float((np.abs(t_pred) > crit).mean()))

xg = np.linspace(-6, 6, 900)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=t_pred,
        nbinsx=140,
        histnorm="probability density",
        name="prior-predictive samples",
        opacity=0.6,
    )
)
fig.add_trace(go.Scatter(x=xg, y=t.pdf(xg, nu), name="central t (delta=0)", mode="lines"))
fig.update_layout(
    title=f"Prior predictive distribution of T (nu={nu}, prior d ~ N(0, {tau}^2))",
    xaxis_title="t statistic",
    yaxis_title="density",
)
fig.show()


Prior predictive P(reject H0): 0.3202083333333333
